# Importando bibliotecas

In [1]:
import logging
import matplotlib.pyplot as plt
from pathlib import Path
import numpy as np
import pandas as pd
from stable_baselines3 import DQN
from stable_baselines3.dqn.policies import MlpPolicy
from datetime import datetime
from sklearn.preprocessing import StandardScaler
import time
from datetime import datetime
from torch import nn  # Import the neural network module from PyTorch
from sklearn.model_selection import train_test_split
from stable_baselines3 import DQN, PPO
from stable_baselines3.dqn.policies import MlpPolicy
from stable_baselines3.common.env_util import make_vec_env
from stable_baselines3.common.vec_env import VecEnv
from stable_baselines3.common.evaluation import evaluate_policy
from sklearn.utils import resample
from tensorflow.keras.models import load_model

import sys
from stable_baselines3 import A2C

import os
sys.path.append(os.path.join('..'))
from classes._exploration import exploration
from classes._Env3WGym import Env3WGym
from classes._LoadInstances import LoadInstances
from classes._Agent import Agent
from classes._Supervised import Supervised
from classes._ValidationModel import ValidationModel
from classes._exploration import exploration

# Validação dos dados simulados

In [2]:
if __name__ == '__main__':

    events_names = {
        # 0: 'Normal',
        1: 'Abrupt Increase of BSW',
        # 2: 'Spurious Closure of DHSV',
        # 3: 'Severe Slugging',
        # 4: 'Flow Instability',
        # 5: 'Rapid Productivity Loss',
        # 6: 'Quick Restriction in PCK',
        # 7: 'Scaling in PCK',
        # 8: 'Hydrate in Production Line'
    }

    event_name = [value for key, value in events_names.items() if key != 0][0]
    
    models = ['DQN' , 'PPO', 'A2C'] # 'DQN' , 'PPO', 'A2C', 'RNA'
    type_instance='real'
    path_dataset = '..\\..\\..\\dataset'
    instances = LoadInstances(path_dataset)
            
    logging.info(f'Iniciando carregamento do dataset')
    dataset, _ = instances.load_instance_with_numpy(events_names, type_instance=type_instance)    
    logging.info(f'Fim carregamento do dataset')
    
    logging.info(f'Iniciando divisão do dataset em treino e teste')
        
    # Definindo a porcentagem para divisão entre treino e teste
    train_percentage = 0.8  # 80% para treino

    dataset_train_scaled, dataset_test_scaled, dataset_validation_scaled = instances.data_preparation(dataset, train_percentage)
    
    for model_type in models:
        for event_name in [value for key, value in events_names.items() if key != 0]:

            directory = f'..\\..\\logs\\{event_name}-{type_instance}'               
            path_model = f'..\\models\\{event_name}-{type_instance}\\{model_type}'  

            if not os.path.exists(directory):
                os.makedirs(directory)
            
            if not os.path.exists(path_model):
                os.makedirs(path_model)   
                    
            current_time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
            log_filename = f'{directory}\\{current_time}_{event_name}-{type_instance}_{model_type}-log.txt'
            # Configuração do Logging
            logging.basicConfig(filename=log_filename, filemode='w', level=logging.INFO, format='[%(levelname)s]\t%(asctime)s - %(message)s', datefmt='%d/%m/%Y %I:%M:%S %p', force=True, encoding='utf-8')

            agente = Agent(path_model, dataset_train_scaled, dataset_test_scaled, n_envs=5, n_envs_eval = 1)

            if model_type == 'DQN':
                
                try:
                    logging.info(f'Iniciando treinamento do algoritmo DQN')    
                    start_time = time.time()                
                    model_agent, replaydir = agente.env3W_dqn()  
                    print(f"Tempo de Treinamento DQN: {round(time.time() - start_time, 2)}s")
                    logging.info(f"Tempo de Treinamento DQN: {round(time.time() - start_time, 2)}s")
                    logging.info(f'Fim treinamento do algoritmo DQN')

                    try:
                        logging.info(f'Iniciando avaliação do algoritmo DQN conjunto de teste')
                        accuracy = agente.env3W_dqn_eval(model = model_agent)
                        print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando DQN')
                        logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando DQN')
                        logging.info(f'Fim avaliação  do algoritmo DQN conjunto de teste')
                    except Exception as e:
                        logging.error(f'Erro ao avaliar o modelo DQN: {e}')

                except Exception as e:
                    logging.error(f'Erro ao treinar o modelo DQN: {e}')
                
            elif model_type == 'PPO':      
                
               
                logging.info(f'Iniciando treinamento do algoritmo PPO') 
                start_time = time.time()
                #agente = Agent(path_model)
                model_agent = agente.env3W_ppo()  
                print(f"Tempo de Treinamento PPO: {round(time.time() - start_time, 2)}s")
                logging.info(f"Tempo de Treinamento PPO: {round(time.time() - start_time, 2)}s")
                logging.info(f'Fim treinamento do algoritmo PPO')
            
                
                logging.info(f'Iniciando avaliação do algoritmo PPO conjunto de teste')
                accuracy = agente.env3W_ppo_eval(model = model_agent)
                print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando PPO')
                logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando PPO')
                logging.info(f'Fim avaliação  do algoritmo PPO conjunto de teste')
               
            elif model_type == 'A2C': 

                try:     
                    logging.info(f'Iniciando treinamento do algoritmo A2C') 
                    start_time = time.time()
                    #agente = Agent(path_model)
                    model_agent = agente.env3W_a2c()  
                    print(f"Tempo de Treinamento A2C: {round(time.time() - start_time, 2)}s")
                    logging.info(f"Tempo de Treinamento A2C: {round(time.time() - start_time, 2)}s")
                    logging.info(f'Fim treinamento do algoritmo A2C')
                
                    try:
                        logging.info(f'Iniciando avaliação do algoritmo A2C conjunto de teste')
                        accuracy = agente.env3W_a2c_eval(model = model_agent)
                        print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando A2C')
                        logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando A2C')
                        logging.info(f'Fim avaliação  do algoritmo A2C conjunto de teste')
                    except Exception as e:
                        logging.error(f'Erro ao avaliar o modelo A2C: {e}')

                except Exception as e:
                    logging.error(f'Erro ao treinar o modelo A2C: {e}')
            
            elif model_type == 'RNA':
                try:
                    logging.info(f'Iniciando treinamento do modelo RNA') 
                    supervised = Supervised(path_model, dataset_train_scaled, dataset_test_scaled)
                    start_time = time.time()
                    model_agent = supervised.keras_train()  
                    print(f"Tempo de Treinamento RNA: {round(time.time() - start_time, 2)}s")
                    logging.info(f"Tempo de Treinamento RNA: {round(time.time() - start_time, 2)}s")
                    logging.info(f'Fim treinamento do modelo RNA')

                    try:
                        logging.info(f'Iniciando avaliação do modelo RNA conjunto de teste')
                        accuracy = supervised.keras_evaluate(model_agent)
                        print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando RNA')
                        logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando RNA')
                        logging.info(f'Fim avaliação  do modelo RNA conjunto de teste')
                    except Exception as e:
                        logging.error(f'Erro ao treinar o modelo RNA: {e}')
                except Exception as e:
                    logging.error(f'Erro ao treinar o modelo RNA: {e}')

            #logging.info(f'Iniciando a validação do modelo {model_type}') 
            #validation = ValidationModel(model_type, event_name)
            #validation.validation_model(accuracy, dataset_validation_scaled, model_agent)

            logging.info(f'Concluído a execução do algoritmo {model_type}-{type_instance} para o evento {event_name}')
            # Para fechar explicitamente o arquivo de log, obtenha todos os handlers do root logger e feche-os
            for handler in logging.root.handlers[:]:
                handler.close()
                logging.root.removeHandler(handler)
   

Número de amostras da classe 0.0: 195376
Número de amostras da classe 1.0: 10417
Número de amostras da classe 101.0: 95658


c:\Python311\Lib\site-packages\stable_baselines3\common\vec_env\patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(


TensorBoard started at http://localhost:6006/
Para visualizar os logs do TensorBoard, execute:
tensorboard --logdir='..\models\Abrupt Increase of BSW-real\tensorboard_logs'
Using cpu device
Logging to ..\models\Abrupt Increase of BSW-real\tensorboard_logs\DQN_0
----------------------------------
| epsilon             | 0.0149   |
| reward_avg          | -0.307   |
| reward_max          | 1.0      |
| reward_min          | -1.0     |
| rollout/            |          |
|    exploration_rate | 0.0149   |
----------------------------------
----------------------------------
| epsilon             | 0.01     |
| reward_avg          | -0.31    |
| reward_max          | 1.0      |
| reward_min          | -1.0     |
| rollout/            |          |
|    exploration_rate | 0.01     |
| train/              |          |
|    learning_rate    | 1e-05    |
|    loss             | 0.179    |
|    n_updates        | 199      |
----------------------------------
----------------------------------
| e

c:\Python311\Lib\site-packages\stable_baselines3\common\logger.py:217: UserWarning: Tried to write empty key-value dict
  warnings.warn("Tried to write empty key-value dict")


----------------------------------
| epsilon             | 0.01     |
| reward_avg          | -0.0888  |
| reward_max          | 1.0      |
| reward_min          | -1.0     |
| rollout/            |          |
|    exploration_rate | 0.01     |
| train/              |          |
|    learning_rate    | 1e-05    |
|    loss             | 0.0307   |
|    n_updates        | 1999     |
----------------------------------
----------------------------------
| epsilon             | 0.01     |
| reward_avg          | -0.0796  |
| reward_max          | 1.0      |
| reward_min          | -1.0     |
| rollout/            |          |
|    exploration_rate | 0.01     |
| train/              |          |
|    learning_rate    | 1e-05    |
|    loss             | 0.0219   |
|    n_updates        | 2199     |
----------------------------------
----------------------------------
| epsilon             | 0.01     |
| reward_avg          | -0.0709  |
| reward_max          | 1.0      |
| reward_min        

c:\Python311\Lib\site-packages\stable_baselines3\common\vec_env\patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(


An error occurred while launching TensorBoard: TensorBoard could not bind to port 6006, it was already in use
Para visualizar os logs do TensorBoard, execute:
tensorboard --logdir='..\models\Abrupt Increase of BSW-real\tensorboard_logs'
Using cpu device
Logging to ..\models\Abrupt Increase of BSW-real\tensorboard_logs\PPO_0
---------------------------------
| reward_avg         | -0.357   |
| reward_max         | 1.0      |
| reward_min         | -1.0     |
| time/              |          |
|    fps             | 2573     |
|    iterations      | 1        |
|    time_elapsed    | 0        |
|    total_timesteps | 25       |
---------------------------------
------------------------------------------
| reward_avg              | -0.333       |
| reward_max              | 1.0          |
| reward_min              | -1.0         |
| time/                   |              |
|    fps                  | 942          |
|    iterations           | 2            |
|    time_elapsed         | 0    

c:\Python311\Lib\site-packages\stable_baselines3\ppo\ppo.py:155: UserWarning: You have specified a mini-batch size of 32, but because the `RolloutBuffer` is of size `n_steps * n_envs = 25`, after every 0 untruncated mini-batches, there will be a truncated mini-batch of size 25
We recommend using a `batch_size` that is a factor of `n_steps * n_envs`.
Info: (n_steps=5 and n_envs=5)
  warnings.warn(


-------------------------------------------
| reward_avg              | -0.349        |
| reward_max              | 1.0           |
| reward_min              | -1.0          |
| time/                   |               |
|    fps                  | 724           |
|    iterations           | 6             |
|    time_elapsed         | 0             |
|    total_timesteps      | 150           |
| train/                  |               |
|    approx_kl            | 2.5987626e-07 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -0.693        |
|    explained_variance   | -0.0523       |
|    learning_rate        | 1e-05         |
|    loss                 | 0.639         |
|    n_updates            | 50            |
|    policy_gradient_loss | -8.69e-05     |
|    value_loss           | 1.28          |
-------------------------------------------
-------------------------------------------
| reward_avg              | -0.3

# Validação com dados reais

In [ ]:
if __name__ == '__main__':

    events_names = {
        # 0: 'Normal',
        1: 'Abrupt Increase of BSW',
        # 2: 'Spurious Closure of DHSV',
        # 3: 'Severe Slugging',
        # 4: 'Flow Instability',
        # 5: 'Rapid Productivity Loss',
        # 6: 'Quick Restriction in PCK',
        # 7: 'Scaling in PCK',
        # 8: 'Hydrate in Production Line'
    }

    event_name = [value for key, value in events_names.items() if key != 0][0]
    
    models = ['DQN'] # 'DQN' or 'PPO', 'RNA', 'A2C'
    type_instance='real'

    for model_type in models:
        for event_name in [value for key, value in events_names.items() if key != 0]:

            directory = f'..\\..\\logs\\{event_name}-{type_instance}'
            path_dataset = '..\\..\\..\\dataset'   
            path_model = f'..\\models\\{event_name}-{type_instance}\\{model_type}'  

            if not os.path.exists(directory):
                os.makedirs(directory)
            
            if not os.path.exists(path_model):
                os.makedirs(path_model)                
            
                    
            current_time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
            log_filename = f'{directory}\\{current_time}_{event_name}-{type_instance}_{model_type}-log.txt'
            # Configuração do Logging
            logging.basicConfig(filename=log_filename, filemode='w', level=logging.INFO, format='[%(levelname)s]\t%(asctime)s - %(message)s', datefmt='%d/%m/%Y %I:%M:%S %p', force=True, encoding='utf-8')

            instances = LoadInstances(path_dataset)
            
            logging.info(f'Iniciando carregamento do dataset')
            dataset, _ = instances.load_instance_with_numpy(events_names, type_instance=type_instance)    
            logging.info(f'Fim carregamento do dataset')
            
            logging.info(f'Iniciando divisão do dataset em treino e teste')
                
            # Definindo a porcentagem para divisão entre treino e teste
            train_percentage = 0.8  # 80% para treino

            dataset_train_scaled, dataset_test_scaled, dataset_validation_scaled = instances.data_preparation(dataset, train_percentage)

            if model_type == 'DQN':
                #logging.info(f'Iniciando treinamento do algoritmo DQN')    
                #start_time = time.time()
                agente = Agent(path_model)
                #model_agent = agente.env3W_dqn(dataset_train_scaled, n_envs = 5)  
                #print(f"Tempo de Treinamento DQN: {round(time.time() - start_time, 2)}s")
                #logging.info(f"Tempo de Treinamento DQN: {round(time.time() - start_time, 2)}s")
                #logging.info(f'Fim treinamento do algoritmo DQN')

                model_agent = DQN.load(f"{path_model.replace('real', 'simulated')}\_DQN_Env3W") 
                logging.info(f'Iniciando avaliação do algoritmo DQN conjunto de teste')
                accuracy = agente.env3W_dqn_eval(dataset_test_scaled, model_agent, n_envs = 1)
                print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando DQN')
                logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando DQN')
                logging.info(f'Fim avaliação  do algoritmo DQN conjunto de teste')
                
                #replay_buffer_path = os.path.join("..", "models", "Abrupt Increase of BSW-simulated", "DQN") # , "replay_buffer"
                logging.info(f'Iniciando treinamento do algoritmo DQN (Continual Learning)')
                model_agent_cl = agente.env3W_dqn_cl(model_agent, dataset_test_scaled, replaydir = replaydir, n_envs = 5)
                logging.info(f'Iniciando avaliação do algoritmo DQN conjunto de teste (Continual Learning)')
                accuracy = agente.env3W_dqn_eval(dataset_test_scaled, model_agent_cl, n_envs = 1)
                print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando DQN (Continual Learning)')
                logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando DQN (Continual Learning)')
                logging.info(f'Fim avaliação  do algoritmo DQN conjunto de teste (Continual Learning)')
                
                
            elif model_type == 'PPO':      
            
                #start_time = time.time()
                agente = Agent(path_model)
                #model_agent = agente.env3W_ppo(dataset_train_scaled, n_envs = 5)  
                #print(f"Tempo de Treinamento PPO: {round(time.time() - start_time, 2)}s")
                #logging.info(f"Tempo de Treinamento PPO: {round(time.time() - start_time, 2)}s")
                #logging.info(f'Fim treinamento do algoritmo PPO')

                
                model_agent = PPO.load(f"{path_model.replace('real', 'simulated')}\_PPO_Env3W")
                logging.info(f'Iniciando avaliação do algoritmo PPO conjunto de teste')
                accuracy = agente.env3W_ppo_eval(dataset_test_scaled, model_agent, n_envs = 1)
                print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando PPO')
                logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando PPO')
                logging.info(f'Fim avaliação  do algoritmo PPO conjunto de teste')

            elif model_type == 'A2C':      
            
                #start_time = time.time()
                agente = Agent(path_model)
                #model_agent = agente.env3W_a2c(dataset_train_scaled, n_envs = 5)  
                #print(f"Tempo de Treinamento A2C: {round(time.time() - start_time, 2)}s")
                #logging.info(f"Tempo de Treinamento A2C: {round(time.time() - start_time, 2)}s")
                #logging.info(f'Fim treinamento do algoritmo A2C')

                model_agent = A2C.load(f"{path_model.replace('real', 'simulated')}/_A2C_Env3W")

                logging.info(f'Iniciando avaliação do algoritmo A2C conjunto de teste')
                accuracy = agente.env3W_a2c_eval(dataset_test_scaled, model_agent, n_envs = 1)
                print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando A2C')
                logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando A2C')
                logging.info(f'Fim avaliação  do algoritmo A2C conjunto de teste')
            
            elif model_type == 'RNA':
                #logging.info(f'Iniciando treinamento do modelo RNA')  
                
                supervised = Supervised(os.path.dirname(path_model.replace('real', 'simulated')), dataset_train_scaled, dataset_test_scaled)
                #start_time = time.time()
                #model_agent = supervised.keras_train()  
                #print(f"Tempo de Treinamento RNA: {round(time.time() - start_time, 2)}s")
                #logging.info(f"Tempo de Treinamento RNA: {round(time.time() - start_time, 2)}s")
                #logging.info(f'Fim treinamento do modelo RNA')
                
                model_agent = supervised.keras_load_model("RNA_Env3W") # Reinforcement-Learning\src\models\Abrupt Increase of BSW-simulated\RNA_Env3W
                
                logging.info(f'Iniciando avaliação do modelo RNA conjunto de teste')
                accuracy = supervised.keras_evaluate(model_agent)
                print(f'Acurácia de {accuracy * 100:.2f}% no conjunto de dados de teste usando RNA')
                logging.info(f'Acurácia de {accuracy:.5f} no conjunto de dados de teste usando RNA')
                logging.info(f'Fim avaliação  do modelo RNA conjunto de teste')

            #logging.info(f'Iniciando a validação do modelo {model_type}') 
            validation = ValidationModel(model_type, event_name)

            validation.validation_model(accuracy, dataset_validation_scaled, model_agent)

            logging.info(f'Concluído a execução do algoritmo {model_type}-{type_instance} para o evento {event_name}')

    # Para fechar explicitamente o arquivo de log, obtenha todos os handlers do root logger e feche-os
    for handler in logging.root.handlers[:]:
        handler.close()
        logging.root.removeHandler(handler)
    

# Exploração dos dados

In [ ]:
'''events_names = {
    # 0: 'Normal',
    1: 'Abrupt Increase of BSW',
    # 2: 'Spurious Closure of DHSV',
    # 3: 'Severe Slugging',
    # 4: 'Flow Instability',
    # 5: 'Rapid Productivity Loss',
    # 6: 'Quick Restriction in PCK',
    # 7: 'Scaling in PCK',
    # 8: 'Hydrate in Production Line'
}

event_name = [value for key, value in events_names.items() if key != 0][0]


type_instance='simulated'

instances = LoadInstances(path_dataset)
            

dataset, _ = instances.load_instance_with_numpy(events_names, type_instance=type_instance)'''

In [ ]:


'''explora = exploration(pd.DataFrame(dataset, columns=['timestamp', 'P-PDG', 'P-TPT', 'T-TPT', 'P-MON-CKP', 'T-JUS-CKP', 'class']))

explora.quartiles_plot(['P-PDG', 'P-TPT', 'T-TPT', 'P-MON-CKP', 'T-JUS-CKP'], f'Quartis das variáveis {type_instance} do evento {event_name}')'''